In [ ]:
%matplotlib inline


# Sobol' analysis


In [ ]:
import pprint

from gemseo.algos.parameter_space import ParameterSpace
from gemseo.api import create_discipline
from gemseo.uncertainty.sensitivity.sobol.analysis import SobolAnalysis
from matplotlib import pyplot as plt
from numpy import pi

In this example,
we consider a function from $[-\pi,\pi]^3$ to $\mathbb{R}^3$:

\begin{align}(y_1,y_2)=\left(f(x_1,x_2,x_3),f(x_2,x_1,x_3)\right)\end{align}

where $f(a,b,c)=\sin(a)+7\sin(b)^2+0.1*c^4\sin(a)$ is the Ishigami function:



In [ ]:
expressions = {
    "y1": "sin(x1)+7*sin(x2)**2+0.1*x3**4*sin(x1)",
    "y2": "sin(x2)+7*sin(x1)**2+0.1*x3**4*sin(x2)",
}
discipline = create_discipline(
    "AnalyticDiscipline", expressions=expressions, name="Ishigami2"
)

Then,
we consider the case where
the deterministic variables $x_1$, $x_2$ and $x_3$ are replaced
with the uncertain variables $X_1$, $X_2$ and $X_3$.
The latter are independent and identically distributed
according to an uniform distribution between $-\pi$ and $\pi$:



In [ ]:
space = ParameterSpace()
for variable in ["x1", "x2", "x3"]:
    space.add_random_variable(
        variable, "OTUniformDistribution", minimum=-pi, maximum=pi
    )

From that,
we would like to carry out a sensitivity analysis with the random outputs
$Y_1=f(X_1,X_2,X_3)$ and $Y_2=f(X_2,X_1,X_3)$.
For that,
we can compute the correlation coefficients from a :class:`.SobolAnalysis`:



In [ ]:
sobol = SobolAnalysis([discipline], space, 100)
sobol.main_method = "total"
sobol.compute_indices()

The resulting indices are the first and total order Sobol' indices:



In [ ]:
pprint.pprint(sobol.indices)

They can also be accessed separately:



In [ ]:
pprint.pprint(sobol.first_order_indices)
pprint.pprint(sobol.total_order_indices)

The main indices corresponds to the Spearman correlation indices
(this main method can be changed with :attr:`.SobolAnalysis.main_method`):



In [ ]:
pprint.pprint(sobol.main_indices)

pprint.pprint(sobol.get_intervals())

We can also sort the input parameters by decreasing order of influence:
and observe that this ranking is not the same for both outputs:



In [ ]:
print(sobol.sort_parameters("y1"))
print(sobol.sort_parameters("y2"))

Lastly,
we can use the method :meth:`.SobolAnalysis.plot`
to visualize both first and total order Sobol' indices:



In [ ]:
sobol.plot("y1", save=False, show=False)
sobol.plot("y2", save=False, show=False)
# Workaround for HTML rendering, instead of ``show=True``
plt.show()